In [1]:
import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
import requests # requests for the report website
import json
from sec_edgar_api import EdgarClient
from bs4 import BeautifulSoup # Import BeautifulSoup
import re # import re module for REGEXes
import time
import os
import html2text
import codecs

# Split eaech sentences
import nltk
from nltk.tokenize import sent_tokenize
nltk.download('punkt')

import yfinance as yf

# Create a folder for save data
#os.mkdir('Data') 


[nltk_data] Downloading package punkt to /Users/qjy/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [2]:
df=pd.read_excel('Semi.xlsx')
df = df[1:]
#df['Unnamed: 1'] = df['Unnamed: 1'].str.replace(' US Equity', '', regex=False)
df['Unnamed: 1'] = df['Unnamed: 1'].str.replace(r' \b\w{2} Equity\b', '', regex=True)
display(df)

Unnamed: 0 Unnamed: 1      Unnamed: 2     Unnamed: 3  \
1             ACM Research Inc       ACMR  Semiconductors  United States   
2    ACM Research Shanghai Inc     688082  Semiconductors          China   
3                   AIXTRON SE       AIXA  Semiconductors        Germany   
4                     ALI Corp       3041  Semiconductors         Taiwan   
5        AMPOC Far-East Co Ltd       2493  Semiconductors         Taiwan   
..                         ...        ...             ...            ...   
331               ams-OSRAM AG        AMS  Semiconductors    Switzerland   
332                eMagin Corp       EMAN  Semiconductors  United States   
333     eMemory Technology Inc       3529  Semiconductors         Taiwan   
334                inTEST Corp       INTT  Semiconductors  United States   
335          u-blox Holding AG       UBXN  Semiconductors    Switzerland   

    Unnamed: 4 Unnamed: 5 Unnamed: 6 Unnamed: 7 Unnamed: 8 Unnamed: 9  \
1     5.476806   5.240198        NaN        NaN        NaN        NaN   
2     4.712091   4.633017        NaN        NaN        NaN        NaN   
3     7.489201   7.718862   7.378706    7.56745   6.514975   6.057901   
4     5.927341   5.805777        NaN        NaN        NaN        NaN   
5     4.639441   3.364894        NaN        NaN        NaN        NaN   
..         ...        ...        ...        ...        ...        ...   
331   7.438245   6.778155   6.435386     4.9636   4.639704   4.184048   
332   5.692832   6.241877        NaN        NaN        NaN        NaN   
333   4.644642   4.623852    5.02783   5.158579   5.199798   5.461997   
334   6.971581   7.024734        NaN        NaN        NaN        NaN   
335   7.752711   6.884037        NaN        NaN        NaN        NaN   

    Unnamed: 10 Unnamed: 11  
1           NaN         NaN  
2           NaN         NaN  
3      5.416154     5.28823  
4           NaN         NaN  
5           NaN         NaN  
..          ...         ...  
331    4.133049    4.814106  
332         NaN         NaN  
333    5.835757    5.570335  
334         NaN         NaN  
335         NaN         NaN  

[335 rows x 12 columns]

In [3]:
CompanyTickers = requests.get('https://www.sec.gov/files/company_tickers.json',
                              headers={'User-Agent':"test@gmail.com"})

CompanyTicker = open('CompanyTickers.json','w+')
CompanyTicker.write(json.dumps(CompanyTickers.json()))
CompanyTicker.close()

CompanyData = pd.DataFrame.from_dict(CompanyTickers.json(), orient='index')
display(CompanyData)

cik_str  ticker                           title
0      320193    AAPL                      Apple Inc.
1      789019    MSFT                  MICROSOFT CORP
2     1045810    NVDA                     NVIDIA CORP
3     1652044   GOOGL                   Alphabet Inc.
4     1018724    AMZN                  AMAZON COM INC
...       ...     ...                             ...
9533  1045450  EPR-PE                  EPR PROPERTIES
9534  1712762   BIAFW  bioAffinity Technologies, Inc.
9535  1456772   OPINL  OFFICE PROPERTIES INCOME TRUST
9536  1848334    OKMN           OKMIN RESOURCES, INC.
9537  1981662   NIVFW             NewGenIvf Group Ltd

[9538 rows x 3 columns]

In [4]:
def FindCompanyCik(Ticker):
    for i in CompanyTickers.json().keys():
        if CompanyTickers.json()[i]['ticker'] ==Ticker:
            print(CompanyTickers.json()[i])   # can be not show
            return CompanyTickers.json()[i]['cik_str']
            break
# CompanyName = 'GOOGL'
# Companycik = FindCompanyCik(CompanyName)

In [5]:
def checkExistingof10k (Companycik):
    edgar = EdgarClient(user_agent="test@gmail.com")
    try:
        test = edgar.get_company_concept(cik=Companycik, taxonomy="us-gaap", tag="AccountsPayableCurrent")
        print(test)    #can be not show
        reportRecord = pd.DataFrame.from_dict(test['units']['USD'])
        pass
    except:
        return False
        pass
    # display(reportRecord)
    type='10-K'
    if type in reportRecord['form'].values:
        return True
    else:
        return False 

In [6]:
# counting company quantity in stock
count = 0
industry = []
for name in df['Unnamed: 1']:
    if name in CompanyData['ticker'].values:
        if checkExistingof10k(FindCompanyCik(name))==True:
            count = count + 1
            industry.append(name)
            print(f"No.{count}-{industry}")
    
print(industry) 
print(count)

Exception ignored in: <bound method IPythonKernel._clean_thread_parent_frames of <ipykernel.ipkernel.IPythonKernel object at 0x10bc44f70>>
Traceback (most recent call last):
  File "/Users/qjy/anaconda3/envs/NLP/lib/python3.8/site-packages/ipykernel/ipkernel.py", line 770, in _clean_thread_parent_frames
    def _clean_thread_parent_frames(
KeyboardInterrupt: 


{'cik_str': 1680062, 'ticker': 'ACMR', 'title': 'ACM Research, Inc.'}
{'cik': 1680062, 'taxonomy': 'us-gaap', 'tag': 'AccountsPayableCurrent', 'label': 'Accounts Payable, Current', 'description': "Carrying value as of the balance sheet date of liabilities incurred (and for which invoices have typically been received) and payable to vendors for goods and services received that are used in an entity's business. Used to reflect the current portion of the liabilities (due within one year or within the normal operating cycle if longer).", 'entityName': 'ACM Research, Inc.', 'units': {'USD': [{'end': '2016-12-31', 'val': 5173000, 'accn': '0001193125-17-364926', 'fy': 2017, 'fp': 'Q3', 'form': '10-Q', 'filed': '2017-12-08'}, {'end': '2016-12-31', 'val': 5173000, 'accn': '0001654954-18-002950', 'fy': 2017, 'fp': 'FY', 'form': '10-K', 'filed': '2018-03-23', 'frame': 'CY2016Q4I'}, {'end': '2017-09-30', 'val': 8667000, 'accn': '0001193125-17-364926', 'fy': 2017, 'fp': 'Q3', 'form': '10-Q', 'filed

Exception ignored in: <bound method IPythonKernel._clean_thread_parent_frames of <ipykernel.ipkernel.IPythonKernel object at 0x10bc44f70>>
Traceback (most recent call last):
  File "/Users/qjy/anaconda3/envs/NLP/lib/python3.8/site-packages/ipykernel/ipkernel.py", line 770, in _clean_thread_parent_frames
    def _clean_thread_parent_frames(
KeyboardInterrupt: 


{'cik_str': 316888, 'ticker': 'ASM', 'title': 'AVINO SILVER & GOLD MINES LTD'}
{'cik_str': 937966, 'ticker': 'ASML', 'title': 'ASML HOLDING NV'}
{'cik': 937966, 'taxonomy': 'us-gaap', 'tag': 'AccountsPayableCurrent', 'label': 'Accounts Payable, Current', 'description': "Carrying value as of the balance sheet date of liabilities incurred (and for which invoices have typically been received) and payable to vendors for goods and services received that are used in an entity's business. Used to reflect the current portion of the liabilities (due within one year or within the normal operating cycle if longer).", 'entityName': 'ASML HOLDING NV', 'units': {'EUR': [{'end': '2008-12-31', 'val': 193690000, 'accn': '0000950123-10-018242', 'fy': 2009, 'fp': 'FY', 'form': '20-F/A', 'filed': '2010-02-26', 'frame': 'CY2008Q4I'}, {'end': '2009-12-31', 'val': 206226000, 'accn': '0000950123-10-018242', 'fy': 2009, 'fp': 'FY', 'form': '20-F/A', 'filed': '2010-02-26'}, {'end': '2009-12-31', 'val': 20622600

In [ ]:
print(industry)

In [6]:
def SearchIndexContents(text):
    #IndexContent = re.compile(r'((ITEM \d+\.\ *\s*(.*?)\n))|(Item \d+\.\ *\s*(.*?)\n)').finditer(text)
    IndexContent = re.compile(r'((ITEM\ *\d+\.\ *\s*(.*?)\n))|(Item\ *\d+\.\ *\s*(.*?)\n)', re.IGNORECASE).finditer(text)


    ItemIndex_df = pd.DataFrame([(match.group().strip(), match.start(), match.end()) for match in IndexContent])
    ItemIndex_df.columns = ['Item', 'start', 'end']
    if len(ItemIndex_df) > 16:
        ItemIndex_df = ItemIndex_df[(len(ItemIndex_df)-16):len(ItemIndex_df)]
    ItemIndex_df = ItemIndex_df.reset_index(drop=True)
    display(ItemIndex_df)
    return ItemIndex_df

In [7]:
def Extractedtext(dataframe:pd,Item:int,report:str):
    start_items = dataframe[dataframe['Item'].str.contains(f"ITEM\s+{Item}", case=False, regex=True)]
    #print(start_items['start'])
    end_items = dataframe[dataframe['Item'].str.contains(f"ITEM\s+{Item+1}", case=False, regex=True)]
    #print(end_items['start'])
    if (start_items.empty==True) or (end_items.empty==True):
        #print('All in empty')
        return ""
    else:
        start_index = start_items.iloc[0]['start']
        end_index = end_items.iloc[0]['start']
        extracted_text = report[start_index:end_index].strip()
        extracted_text = re.sub(r'\*|\_|\||\#|\-', '', extracted_text)
        extracted_text = re.sub(r'\n', ' ', extracted_text)
        return(extracted_text)

In [8]:
def ExtractESG(text):
    ReportIndex = SearchIndexContents(text)

    item1 = Extractedtext(ReportIndex,1,text)
    item3 = Extractedtext(ReportIndex,3,text)
    item7 = Extractedtext(ReportIndex,7,text)
    item10 = Extractedtext(ReportIndex,10,text)
    item11 = Extractedtext(ReportIndex,11,text)
    item12 = Extractedtext(ReportIndex,12,text)
    All = item1 + ' '+ item3 +' '+ item7 +' '+ item10 +' '+ item11 +' '+ item12
    Split = sent_tokenize(All)
    
    return Split

In [9]:
def Download10kdata(companyCik,CompanyName,CompanyRec):
    edgar = EdgarClient(user_agent="test@gmail.com")
    test = edgar.get_company_concept(cik=companyCik, taxonomy="us-gaap", tag="AccountsPayableCurrent")
    reportRecord = pd.DataFrame.from_dict(test['units']['USD'])
    Company10K = reportRecord[reportRecord['form']=='10-K']
    Company10K=Company10K.drop_duplicates(['fy'])
    Company10K=Company10K.set_index('fy')
    for i,row in Company10K.iterrows():  
        accn = row['accn']
        print(f'{CompanyName}-{accn}')
        accnid = accn.replace('-','')
        #print(accnid)
        #time.sleep(1)
        try:
            Report_10K = requests.get(f'https://www.sec.gov/Archives/edgar/data/{companyCik}/{accnid}/{accn}.txt',
                              headers={'User-Agent':"test@gmail.com"})
            #print(Report_10K)
            raw_10k = Report_10K.text
            clear10K = html2text.html2text(raw_10k)
            #print(clear10K)
            split = ExtractESG(clear10K)
            #print(split)
            # Create a folder for save data
            df = pd.DataFrame(split)
            df.to_csv(f"ReportSplitSentences/{CompanyName}-{i}.csv",index=False)
            CompanyRec.loc[len(CompanyRec.index)]=[CompanyName,i,companyCik, accn,'True',len(df.index)]
            pass
        except:
            CompanyRec.loc[len(CompanyRec.index)]=[CompanyName,i,companyCik, accn,'False',0]
            pass

In [10]:
Hardware = ['DDD', 'ATEN', 'ADTN', 'AKTS', 'ATEX', 'AAPL', 'AAOI', 'ANET', 'ARLO', 'ALOT', 'AATC', 'AVNW', 'AWRE', 'BDRL', 'CAMP', 'CMBM', 'CIEN', 'CSCO', 'CLRO', 'CLFD', 'COMM', 'CMTL', 'GLW', 'CRSR', 'CXT', 'CRDO', 'DZSI', 'DAKT', 'DELL', 'DM', 'DBD', 'DLB', 'EMKR', 'EXTR', 'FFIV', 'FEIM', 'GRMN', 'GPRO', 'HPQ', 'HLIT', 'HPE', 'INVE', 'INFN', 'INSG', 'IDCC', 'JNPR', 'KN', 'KOPN', 'KOSS', 'LTRX', 'LITE', 'LUNA', 'MVIS', 'MSI', 'VYX', 'NTGR', 'NEON', 'NTAP', 'NTCT', 'PAR', 'AGS', 'PWFL', 'PSTG', 'QMCO', 'REKR', 'STX', 'SGHT', 'SNPO', 'SONM', 'SONO', 'SMCI', 'TTMI', 'TDY', 'TACT', 'HEAR', 'UI', 'UEIC', 'VOXX', 'VSAT', 'VIAV', 'VICR', 'VZIO', 'VUZI', 'WDC', 'XRX', 'ZBRA']
Semi =['ACMR', 'AXTI', 'AMD', 'AOSL', 'AMBA', 'AMKR', 'ASYS', 'ADI', 'AMAT', 'AIP', 'ATOM', 'ACLS', 'AVGO', 'CRUS', 'COHR', 'COHU', 'DIOD', 'ENTG', 'FORM', 'GSIT', 'IPGP', 'PI', 'INTC', 'IDN', 'KLAC', 'KLIC', 'LRCX', 'LSCC', 'MTSI', 'MKSI', 'MX', 'MRVL', 'MXL', 'MCHP', 'MPWR', 'NVEC', 'NVDA', 'NXPI', 'NMGX', 'NLST', 'ON', 'ONTO', 'OUST', 'PRKR', 'PRSO', 'PLAB', 'PXLW', 'POWI', 'QCOM', 'QRVO', 'RMBS', 'RELL', 'RBT', 'SGH', 'SOI', 'SMTC', 'SENS', 'SITM', 'SLAB', 'SKYT', 'SWKS', 'SYNA', 'TER', 'TXN', 'UCTT', 'OLED', 'VECO', 'VSH', 'WOLF', 'AMS', 'INTT']
Mix = Hardware + Semi
print(Mix)

['DDD', 'ATEN', 'ADTN', 'AKTS', 'ATEX', 'AAPL', 'AAOI', 'ANET', 'ARLO', 'ALOT', 'AATC', 'AVNW', 'AWRE', 'BDRL', 'CAMP', 'CMBM', 'CIEN', 'CSCO', 'CLRO', 'CLFD', 'COMM', 'CMTL', 'GLW', 'CRSR', 'CXT', 'CRDO', 'DZSI', 'DAKT', 'DELL', 'DM', 'DBD', 'DLB', 'EMKR', 'EXTR', 'FFIV', 'FEIM', 'GRMN', 'GPRO', 'HPQ', 'HLIT', 'HPE', 'INVE', 'INFN', 'INSG', 'IDCC', 'JNPR', 'KN', 'KOPN', 'KOSS', 'LTRX', 'LITE', 'LUNA', 'MVIS', 'MSI', 'VYX', 'NTGR', 'NEON', 'NTAP', 'NTCT', 'PAR', 'AGS', 'PWFL', 'PSTG', 'QMCO', 'REKR', 'STX', 'SGHT', 'SNPO', 'SONM', 'SONO', 'SMCI', 'TTMI', 'TDY', 'TACT', 'HEAR', 'UI', 'UEIC', 'VOXX', 'VSAT', 'VIAV', 'VICR', 'VZIO', 'VUZI', 'WDC', 'XRX', 'ZBRA', 'ACMR', 'AXTI', 'AMD', 'AOSL', 'AMBA', 'AMKR', 'ASYS', 'ADI', 'AMAT', 'AIP', 'ATOM', 'ACLS', 'AVGO', 'CRUS', 'COHR', 'COHU', 'DIOD', 'ENTG', 'FORM', 'GSIT', 'IPGP', 'PI', 'INTC', 'IDN', 'KLAC', 'KLIC', 'LRCX', 'LSCC', 'MTSI', 'MKSI', 'MX', 'MRVL', 'MXL', 'MCHP', 'MPWR', 'NVEC', 'NVDA', 'NXPI', 'NMGX', 'NLST', 'ON', 'ONTO', 'OUST',

In [11]:
downloadRec = pd.DataFrame(columns=['CompanyTicker','Year','CIK', 'ACCN','Status','CSV.Length'])
for item in Mix:
        CompanyName = item
        Companycik = FindCompanyCik(CompanyName)
        Download10kdata(Companycik,CompanyName,downloadRec)
        
print(downloadRec)

{'cik_str': 910638, 'ticker': 'DDD', 'title': '3D SYSTEMS CORP'}
DDD-0001193125-12-074109


Item   start     end
0   Item  15.** |    | **Exhibits, Financial State...    7449    7533
1                  Item 1.** | ******_Business_******    7589    7626
2                Item 2.** | ******_Properties_******   95080   95119
3        Item 3.** | ******_Legal Proceedings._******   97978   98025
4   Item 4.** | ******_Mine Safety Disclosures_******  101746  101798
5   Item 5.** | ******_Market for Registrant s Co...  101846  102021
6   Item 6.** | ******_Selected Financial Data_******  107838  107890
7   Item 7.** | ******_Management s Discussion an...  113584  113699
8   Item 8.** | ******_Financial Statements and Su...  226473  226545
9   Item 9.** | ******_Changes in and Disagreement...  226681  226794
10  Item 10.** | ******_Directors, Executive Offic...  232784  232868
11  Item 11.** | ******_Executive Compensation_******  233413  233465
12  Item 12.** | ******_Security Ownership of Cert...  233852  233976
13  Item 13.** | ******_Certain Relationships and ...  235489  235591
14  Item 14.** | ******_Principal Accounting Fees ...  235960  236028
15  Item 15.** | ******_Exhibits, Financial Statem...  236353  236422

DDD-0001193125-13-072822


Item  start   end
0             Item 1. |    |  Business |    |   | 2 |   5334  5379
1          Item 2. |    |  Properties |    |   | 24 |   5515  5563
2   Item 3. |    |  Legal Proceedings. |    |   | ...   5570  5626
3   Item 4. |    |  Mine Safety Disclosures |    |...   5633  5694
4   Item 5. |    |  Market for Registrants Common...   5749  5932
5   Item 6. |    |  Selected Financial Data |    |...   5939  6000
6   Item 7. |    |  Managements Discussion and An...   6007  6130
7   Item 8. |    |  Financial Statements and Suppl...   6241  6322
8   Item 9. |    |  Changes in and Disagreements w...   6329  6451
9   Item 10. |    |  Directors, Executive Officers...   6639  6732
10  Item 11. |    |  Executive Compensation |    |...   6739  6800
11  Item 12. |    |  Security Ownership of Certain...   6807  6940
12  Item 13. |    |  Certain Relationships and Rel...   6947  7058
13  Item 14. |    |  Principal Accounting Fees and...   7065  7142
14  Item 15. |    |  Exhibits, Financial Statement...   7197  7275

DDD-0001562762-14-000032


...

INTT-0001437749-23-007539


Item   start     end
0                         Item 2.** |  **PROPERTIES**  140939  140969
1                  Item 3.** |  **LEGAL PROCEEDINGS**  142488  142525
2            Item 4.** |  **MINE SAFETY DISCLOSURES**  142720  142763
3   Item 5.** |  **MARKET FOR REGISTRANT'S COMMON ...  142808  142936
4             Item 12. "Security Ownership of Certain  145404  145444
5                           Item 6.** |  **RESERVED**  145571  145599
6   Item 7.** |  **MANAGEMENT'S DISCUSSION AND ANA...  145614  145719
7   Item 8.** |  **FINANCIAL STATEMENTS AND SUPPLE...  193963  194026
8   Item 8.\n\n**Item 9.** |  **CHANGES IN AND DIS...  194168  194283
9   Item 10.** |  **DIRECTORS, EXECUTIVE OFFICERS ...  199582  199657
10           Item 11.** |  **EXECUTIVE COMPENSATION**  200358  200401
11  Item 12.** |  **SECURITY OWNERSHIP OF CERTAIN ...  200665  200780
12  Item 13.** |  **CERTAIN RELATIONSHIPS AND RELA...  202458  202552
13  Item 14.** |  **PRINCIPAL ACCOUNTING FEES AND ...  202816  202875
14  Item 15.** |  **EXHIBITS, FINANCIAL STATEMENT ...  203152  203212
15                Item 16.** |  **FORM 10-K SUMMARY**  204226  204264

INTT-0001437749-24-009626


Item   start     end
0                         Item 2.** |  **PROPERTIES**  146222  146252
1                  Item 3.** |  **LEGAL PROCEEDINGS**  148439  148476
2            Item 4.** |  **MINE SAFETY DISCLOSURES**  148660  148703
3   Item 5.** |  **MARKET FOR REGISTRANT'S COMMON ...  148748  148876
4             Item 12. "Security Ownership of Certain  150620  150660
5                           Item 6.** |  **RESERVED**  150787  150815
6   Item 7.** |  **MANAGEMENT'S DISCUSSION AND ANA...  150830  150935
7   Item 8.** |  **FINANCIAL STATEMENTS AND SUPPLE...  198635  198698
8   Item 8.\n\n**Item 9.** |  **CHANGES IN AND DIS...  198840  198955
9   Item 10.** |  **DIRECTORS, EXECUTIVE OFFICERS ...  207078  207153
10           Item 11.** |  **EXECUTIVE COMPENSATION**  207854  207897
11  Item 12.** |  **SECURITY OWNERSHIP OF CERTAIN ...  208161  208276
12  Item 13.** |  **CERTAIN RELATIONSHIPS AND RELA...  210009  210103
13  Item 14.** |  **PRINCIPAL ACCOUNTING FEES AND ...  210367  210426
14  Item 15.** |  **EXHIBITS, FINANCIAL STATEMENT ...  210703  210763
15                Item 16.** |  **FORM 10-K SUMMARY**  211778  211816

     CompanyTicker  Year      CIK                  ACCN Status  CSV.Length
0              DDD  2011   910638  0001193125-12-074109   True         985
1              DDD  2012   910638  0001193125-13-072822   True          10
2              DDD  2013   910638  0001562762-14-000032   True        1024
3              DDD  2014   910638  0000910638-15-000003   True        1539
4              DDD  2015   910638  0000910638-16-000016   True         862
...            ...   ...      ...                   ...    ...         ...
1705          INTT  2019  1036262  0001437749-20-005921   True         230
1706          INTT  2020  1036262  0001437749-21-006901   True         799
1707          INTT  2021  1036262  0001437749-22-006956   True         838
1708          INTT  2022  1036262  0001437749-23-007539   True         608
1709          INTT  2023  1036262  0001437749-24-009626   True         596

[1710 rows x 6 columns]
